In [191]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error
from catboost import CatBoostRegressor
from xgboost import XGBRegressor

In [192]:
df = pd.read_csv('C:/Users/markc/Downloads/houses/train.csv')

**Удаляем колонки, где NaN-ов слишком много или один класс сильно преобладает над другими (96%+)**

In [193]:
df.drop(['PoolQC', 'MiscFeature', 'Alley', 'Fence', 'Street', 'Utilities', 'Condition2', 'RoofMatl', 'Heating', 
         'GarageCond', '3SsnPorch', 'ScreenPorch', 'BsmtFinSF2', 'LowQualFinSF', 'PoolArea', 'MiscVal'], 
        axis=1, inplace=True)

**Удаляем строки, где NaN-ы в тотальном большинстве Bsmt-колонок**

In [194]:
df.drop(df[df.BsmtQual.isna()].index, inplace=True)
df = df.reset_index(drop=True)

**Удаляем строки, где NaN-ы в тотальном большинстве Garage-колонок**

In [195]:
df.drop(df[df.GarageType.isna()].index, inplace=True)
df = df.reset_index(drop=True)

**Выделяем таргет и id**

In [196]:
y = df.SalePrice
df.drop(['SalePrice'], axis=1, inplace=True)

In [197]:
df_id = df.Id
df.drop(['Id'], axis=1, inplace=True)

**Заполняем NaN-ы в LotFrontage**

In [198]:
df.loc[df['LotFrontage'].isna(), 'LotFrontage'] = df[(df.LotFrontage.notna()) & 
                                                     (df.LotShape == 'IR1') & 
                                                     (df.LotConfig == 'Inside')].LotFrontage.mean() + 1

**Заполняем NaN-ы в MasVnrType и MasVnrArea**

In [199]:
df[(df.MasVnrArea.notna()) & (df.OverallCond == 5) & (df.RoofStyle == 'Gable') & (df.ExterQual == 'Gd') & (df.ExterCond == 'TA') & 
   (df.Foundation == 'PConc') & (df.BsmtQual == 'Gd') & (df.BsmtCond == 'TA') & (df.BsmtExposure == 'No')].MasVnrArea.mean()

109.9281045751634

In [200]:
df.loc[df.MasVnrType.isna(), 'MasVnrType'] = 'None'

In [201]:
df.loc[df.MasVnrArea.isna(), 'MasVnrArea'] = 109.9281045751634 + 1

**Заполняем NaN-ы в BsmtExposure**

In [202]:
df[(df.BsmtQual == 'Gd') & (df.BsmtCond == 'TA') & (df.BsmtFinType1 == 'Unf')].BsmtExposure.value_counts() # поиск похожих строчек

No    133
Av     26
Mn     10
Gd      5
Name: BsmtExposure, dtype: int64

In [203]:
df.loc[df.BsmtExposure.isna(), 'BsmtExposure'] = 'No'

**Заполняем NaN-ы в BsmtFinType2**

In [204]:
df[(df.BsmtQual == 'Gd') & (df.BsmtCond == 'TA') & (df.BsmtFinType1 == 'GLQ') & (df.BsmtExposure == 'No')].BsmtFinType2.value_counts() # поиск похожих строчек

Unf    124
LwQ      1
Rec      1
Name: BsmtFinType2, dtype: int64

In [205]:
df.loc[df.BsmtFinType2.isna(), 'BsmtFinType2'] ='Unf'

**Заполняем NaN-ы в Electrical**

In [206]:
df.Electrical.value_counts()

SBrkr    1252
FuseA      76
FuseF      17
FuseP       2
Mix         1
Name: Electrical, dtype: int64

In [207]:
df.loc[df.Electrical.isna(), 'Electrical'] ='SBrkr'

**Заполняем NaN-ы в FireplaceQu**

In [208]:
features = ['YearRemodAdd', 'MasVnrArea', 'TotalBsmtSF', '1stFlrSF'] # колонки с наибольшей корреляцией с FireplaceQu

In [209]:
df[df.FireplaceQu.notna()].groupby(df.FireplaceQu)['1stFlrSF'].describe()

count         mean         std    min     25%     50%     75%  \
FireplaceQu                                                                  
Ex            23.0  1708.869565  388.733176  816.0  1497.0  1675.0  1960.0   
Fa            33.0  1180.666667  252.992177  660.0  1056.0  1186.0  1309.0   
Gd           373.0  1350.809651  459.320142  572.0  1028.0  1301.0  1632.0   
Po            17.0  1039.529412  241.743696  483.0   900.0  1092.0  1154.0   
TA           307.0  1242.635179  345.180398  561.0   978.0  1203.0  1465.0   

                max  
FireplaceQu          
Ex           2444.0  
Fa           1679.0  
Gd           4692.0  
Po           1465.0  
TA           2515.0

In [210]:
df.loc[(df.FireplaceQu.isna()) & (df['1stFlrSF'] >= 1708) , 'FireplaceQu'] = 'Ex'
df.loc[(df.FireplaceQu.isna()) & (df['1stFlrSF'] >= 1350) & (df['1stFlrSF'] < 1708), 'FireplaceQu'] = 'Gd'
df.loc[(df.FireplaceQu.isna()) & (df['1stFlrSF'] >= 1242) & (df['1stFlrSF'] < 1350), 'FireplaceQu'] = 'TA'
df.loc[(df.FireplaceQu.isna()) & (df['1stFlrSF'] >= 1155) & (df['1stFlrSF'] < 1242), 'FireplaceQu'] = 'Fa'
df.loc[(df.FireplaceQu.isna()) & (df['1stFlrSF'] < 1155), 'FireplaceQu'] = 'Po'

**Меняем тип в колонке GarageYrBlt**

In [211]:
df = df.astype({'GarageYrBlt': np.int64})
df = df.astype({'MasVnrArea': np.int64})
df = df.astype({'LotFrontage': np.int64})

In [212]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1349 entries, 0 to 1348
Data columns (total 63 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   MSSubClass     1349 non-null   int64 
 1   MSZoning       1349 non-null   object
 2   LotFrontage    1349 non-null   int64 
 3   LotArea        1349 non-null   int64 
 4   LotShape       1349 non-null   object
 5   LandContour    1349 non-null   object
 6   LotConfig      1349 non-null   object
 7   LandSlope      1349 non-null   object
 8   Neighborhood   1349 non-null   object
 9   Condition1     1349 non-null   object
 10  BldgType       1349 non-null   object
 11  HouseStyle     1349 non-null   object
 12  OverallQual    1349 non-null   int64 
 13  OverallCond    1349 non-null   int64 
 14  YearBuilt      1349 non-null   int64 
 15  YearRemodAdd   1349 non-null   int64 
 16  RoofStyle      1349 non-null   object
 17  Exterior1st    1349 non-null   object
 18  Exterior2nd    1349 non-null

**Выделяем численные и категориальные колонки**

In [213]:
cols = df.select_dtypes(include="object_").columns

In [214]:
cols

Index(['MSZoning', 'LotShape', 'LandContour', 'LotConfig', 'LandSlope',
       'Neighborhood', 'Condition1', 'BldgType', 'HouseStyle', 'RoofStyle',
       'Exterior1st', 'Exterior2nd', 'MasVnrType', 'ExterQual', 'ExterCond',
       'Foundation', 'BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1',
       'BsmtFinType2', 'HeatingQC', 'CentralAir', 'Electrical', 'KitchenQual',
       'Functional', 'FireplaceQu', 'GarageType', 'GarageFinish', 'GarageQual',
       'PavedDrive', 'SaleType', 'SaleCondition'],
      dtype='object')

In [215]:
real_cols = ['LotFrontage', 'LotArea', 'YearBuilt', 'YearRemodAdd', 'MasVnrArea', 'BsmtFinSF1', 'BsmtUnfSF',
             'TotalBsmtSF', '1stFlrSF', '2ndFlrSF', 'GrLivArea', 'GarageYrBlt', 'GarageArea', 'WoodDeckSF', 
             'OpenPorchSF', 'EnclosedPorch']
cat_cols = ['MSSubClass', 'OverallQual', 'OverallCond', 'BsmtFullBath', 'BsmtHalfBath', 'FullBath', 'HalfBath',
            'BedroomAbvGr', 'KitchenAbvGr', 'TotRmsAbvGrd', 'Fireplaces', 'GarageCars', 'MoSold', 'YrSold', 
            'MSZoning', 'LotShape', 'LandContour', 'LotConfig', 'LandSlope', 'Neighborhood', 'Condition1', 'BldgType', 
            'HouseStyle', 'RoofStyle', 'Exterior1st', 'Exterior2nd', 'MasVnrType', 'ExterQual', 'ExterCond', 
            'Foundation', 'BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2', 'HeatingQC', 
            'CentralAir', 'Electrical', 'KitchenQual', 'Functional', 'FireplaceQu', 'GarageType', 'GarageFinish', 
            'GarageQual', 'PavedDrive', 'SaleType', 'SaleCondition']

**Предобрабатываем данные**

In [216]:
from sklearn.preprocessing import StandardScaler

In [217]:
scaler = StandardScaler()
scaler_real_cols = pd.DataFrame(scaler.fit_transform(df[real_cols]), columns=scaler.get_feature_names_out())

In [218]:
from sklearn.preprocessing import OneHotEncoder, LabelEncoder

In [219]:
#ohe = OneHotEncoder()
label = LabelEncoder()
#one_hot_cat_cols = pd.DataFrame(ohe.fit_transform(cat_cols).toarray())
#label_cat_cols = pd.DataFrame(label.fit_transform(cat_cols).toarray(), columns=label.get_feature_names_out())
label_cat_cols = df[cat_cols].apply(LabelEncoder().fit_transform)

In [220]:
X = pd.concat([scaler_real_cols, label_cat_cols], axis='columns')
X

LotFrontage   LotArea  YearBuilt  YearRemodAdd  MasVnrArea  BsmtFinSF1  \
0       -0.287658 -0.219880   1.006490      0.848170    0.462810    0.522937   
1        0.389410 -0.108347   0.093043     -0.483478   -0.597376    1.114885   
2       -0.152244  0.051680   0.938827      0.798850    0.278900    0.044156   
3       -0.513347 -0.113196  -1.970671     -0.779400   -0.597376   -0.543438   
4        0.569962  0.343607   0.904996      0.700209    1.295813    0.411947   
...           ...       ...        ...           ...         ...         ...   
1344    -0.423071 -0.271573   0.871164      0.700209   -0.597376   -1.013514   
1345     0.615100  0.238377   0.160705      0.108366    0.046308    0.705744   
1346    -0.242520 -0.162465  -1.091056      0.996131   -0.597376   -0.415038   
1347    -0.152244 -0.096999  -0.786573      0.502928   -0.597376   -0.906877   
1348     0.163721 -0.075662  -0.279103     -1.026001   -0.597376    0.792796   

      BsmtUnfSF  TotalBsmtSF  1stFlrSF  2ndFlrSF  ...  Electrical  \
0     -0.984939    -0.590775 -0.828209  1.128072  ...           4   
1     -0.680453     0.398969  0.217856 -0.812007  ...           4   
2     -0.339611    -0.434757 -0.663312  1.155333  ...           4   
3     -0.098749    -0.834555 -0.557675  0.905440  ...           4   
4     -0.212363     0.113747 -0.083596  1.580152  ...           4   
...         ...          ...       ...       ...  ...         ...   
1344   0.839703    -0.354309 -0.578287  0.764591  ...           4   
1345   0.012593     1.081550  2.307409 -0.812007  ...           4   
1346   0.667010     0.130811  0.027194  1.805055  ...           4   
1347  -1.325781    -0.049585 -0.256223 -0.812007  ...           0   
1348  -1.016751     0.384342  0.202397 -0.812007  ...           4   

      KitchenQual  Functional  FireplaceQu  GarageType  GarageFinish  \
0               2           6            3           1             1   
1               3           6            4           1             1   
2               2           6            4           1             1   
3               2           6            2           5             2   
4               2           6            4           1             1   
...           ...         ...          ...         ...           ...   
1344            3           6            4           1             1   
1345            3           2            4           1             2   
1346            2           6            2           1             1   
1347            2           6            3           1             2   
1348            3           6            4           1             0   

      GarageQual  PavedDrive  SaleType  SaleCondition  
0              4           2         8              4  
1              4           2         8              4  
2              4           2         8              4  
3              4           2         8              0  
4              4           2         8              4  
...          ...         ...       ...            ...  
1344           4           2         8              4  
1345           4           2         8              4  
1346           4           2         8              4  
1347           4           2         8              4  
1348           4           2         8              4  

[1349 rows x 63 columns]

In [221]:
from sklearn.model_selection import train_test_split

In [222]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)

**Линейная регрессия**

In [223]:
params_lreg = {'fit_intercept': [True, False]}
grid_lreg = GridSearchCV(LinearRegression(), params_lreg, n_jobs=-1, verbose=2, scoring='neg_root_mean_squared_error')
grid_lreg.fit(X, y)

Fitting 5 folds for each of 2 candidates, totalling 10 fits


GridSearchCV(estimator=LinearRegression(), n_jobs=-1,
             param_grid={'fit_intercept': [True, False]},
             scoring='neg_root_mean_squared_error', verbose=2)

In [224]:
grid_lreg.best_params_

{'fit_intercept': True}

In [225]:
grid_lreg.best_score_

-35637.4719812833

In [226]:
lreg = LinearRegression(fit_intercept=True)
lreg.fit(X, y)

LinearRegression()

In [227]:
y_pred = lreg.predict(X_test)

In [228]:
np.sqrt(mean_squared_error(y_test, y_pred))

35175.68308495331

**SVM регрессия** 1 hour 15 min

In [229]:
params_svm = {'kernel': ['linear', 'poly', 'rbf', 'sigmoid'],
              'gamma': ['scale', 'auto'],
              'C': np.arange(0.1, 2.1, 0.1),
              'degree': np.arange(1, 6),
              'coef0': np.arange(0.0, 1.1, 0.1),
              'epsilon': np.arange(0.1, 1.1, 0.1)}
grid_svm = GridSearchCV(SVR(), params_svm, n_jobs=-1, verbose=2, scoring='neg_root_mean_squared_error')
grid_svm.fit(X, y)

Fitting 5 folds for each of 88000 candidates, totalling 440000 fits


KeyboardInterrupt: 

In [ ]:
grid_svm.best_params_

In [ ]:
svm = SVR(C=2.0, coef0=1.0, degree=4, epsilon=1.0, gamma='auto', kernel='poly')
svm.fit(X, y)

In [ ]:
y_pred = svm.predict(X_test)

In [ ]:
np.sqrt(mean_squared_error(y_test, y_pred))

**RandomForest регрессия** 14 min

In [ ]:
params_rndfor = {'n_estimators': range(30, 111),
                 #'criterion': ['squared_error', 'friedman_mse', 'absolute_error', 'poisson']
                 'min_samples_split': [2, 5, 10, 15, 20, 25],
                 'min_samples_leaf': [2, 5, 10, 15, 20, 25]}
grid_rndfor = GridSearchCV(RandomForestRegressor(), params_rndfor, n_jobs=-1, verbose=2, scoring='neg_root_mean_squared_error')
grid_rndfor.fit(X, y)

In [58]:
grid_rndfor.best_params_

{'min_samples_leaf': 2, 'min_samples_split': 5, 'n_estimators': 78}

In [60]:
rndfor = RandomForestRegressor(min_samples_leaf=2, min_samples_split=5, n_estimators=78)
rndfor.fit(X, y)

RandomForestRegressor(min_samples_leaf=2, min_samples_split=5, n_estimators=78)

In [61]:
y_pred = rndfor.predict(X_test)

In [62]:
np.sqrt(mean_squared_error(y_test, y_pred))

12050.00546634549

**XGBoost**

In [301]:
params_xgb = {'n_estimators': [50, 100, 250, 500, 750, 1000],
              'max_depth': [3, 5, 10, 15, 20, 25, 30, 40, 50]}
grid_xgb = GridSearchCV(XGBRegressor(), params_xgb, n_jobs=-1, verbose=2, scoring='neg_root_mean_squared_error')
grid_xgb.fit(X, y)

Fitting 5 folds for each of 54 candidates, totalling 270 fits


GridSearchCV(estimator=XGBRegressor(base_score=None, booster=None,
                                    callbacks=None, colsample_bylevel=None,
                                    colsample_bynode=None,
                                    colsample_bytree=None, device=None,
                                    early_stopping_rounds=None,
                                    enable_categorical=False, eval_metric=None,
                                    feature_types=None, gamma=None,
                                    grow_policy=None, importance_type=None,
                                    interaction_constraints=None,
                                    learning_rate=None, max_bi...
                                    max_cat_to_onehot=None, max_delta_step=None,
                                    max_depth=None, max_leaves=None,
                                    min_child_weight=None, missing=nan,
                                    monotone_constraints=None,
                                    multi_strategy=None, n_estimators=None,
                                    n_jobs=None, num_parallel_tree=None,
                                    random_state=None, ...),
             n_jobs=-1,
             param_grid={'max_depth': [3, 5, 10, 15, 20, 25, 30, 40, 50],
                         'n_estimators': [50, 100, 250, 500, 750, 1000]},
             scoring='neg_root_mean_squared_error', verbose=2)

In [302]:
grid_xgb.best_params_

{'max_depth': 5, 'n_estimators': 50}

In [378]:
xgb = XGBRegressor()
xgb.fit(df, y)

ValueError: DataFrame.dtypes for data must be int, float, bool or category. When categorical type is supplied, The experimental DMatrix parameter`enable_categorical` must be set to `True`.  Invalid columns:MSZoning: object, LotShape: object, LandContour: object, LotConfig: object, LandSlope: object, Neighborhood: object, Condition1: object, BldgType: object, HouseStyle: object, RoofStyle: object, Exterior1st: object, Exterior2nd: object, MasVnrType: object, ExterQual: object, ExterCond: object, Foundation: object, BsmtQual: object, BsmtCond: object, BsmtExposure: object, BsmtFinType1: object, BsmtFinType2: object, HeatingQC: object, CentralAir: object, Electrical: object, KitchenQual: object, Functional: object, FireplaceQu: object, GarageType: object, GarageFinish: object, GarageQual: object, PavedDrive: object, SaleType: object, SaleCondition: object

In [367]:
y_pred = xgb.predict(X_test)

In [368]:
np.sqrt(mean_squared_error(y_test, y_pred))

1041.7060172848642

**CatBoostRegressor**

In [116]:
df.head()

MSSubClass MSZoning  LotFrontage  LotArea LotShape LandContour LotConfig  \
0          60       RL           65     8450      Reg         Lvl    Inside   
1          20       RL           80     9600      Reg         Lvl       FR2   
2          60       RL           68    11250      IR1         Lvl    Inside   
3          70       RL           60     9550      IR1         Lvl    Corner   
4          60       RL           84    14260      IR1         Lvl       FR2   

  LandSlope Neighborhood Condition1  ... GarageArea GarageQual  PavedDrive  \
0       Gtl      CollgCr       Norm  ...        548         TA           Y   
1       Gtl      Veenker      Feedr  ...        460         TA           Y   
2       Gtl      CollgCr       Norm  ...        608         TA           Y   
3       Gtl      Crawfor       Norm  ...        642         TA           Y   
4       Gtl      NoRidge       Norm  ...        836         TA           Y   

   WoodDeckSF  OpenPorchSF  EnclosedPorch MoSold YrSold SaleType SaleCondition  
0           0           61              0      2   2008       WD        Normal  
1         298            0              0      5   2007       WD        Normal  
2           0           42              0      9   2008       WD        Normal  
3           0           35            272      2   2006       WD       Abnorml  
4         192           84              0     12   2008       WD        Normal  

[5 rows x 63 columns]

In [117]:
X_train_boost, X_test_boost, y_train_boost, y_test_boost = train_test_split(df, y,test_size=0.2)

In [118]:
catboost = CatBoostRegressor(cat_features=cat_cols, eval_metric='RMSE', loss_function='RMSE')

In [119]:
PARAMS = {
    "iterations": [1000, 2000, 3000],
    #"learning_rate": [0.01, 0.05, 0.1, 0.5],
    "max_depth": [3, 4, 5, 6, 7, 8, 9]
    #"l2_leaf_reg": np.arange(2.1, 3.1, 0.1),
    #"subsample": np.arange(),
    #"grow_policy": ['SymmetricTree', 'Depthwise', 'Lossguide'], 
    #"random_strength": [1, 2, 5],
    #"min_data_in_leaf": [1, 2, 5, 10, 15]
}
catboost.grid_search(PARAMS, df, y, cv=5, refit=True, verbose=True)

0:	learn: 198349.4770364	test: 194859.9259874	best: 194859.9259874 (0)	total: 148ms	remaining: 2m 28s
1:	learn: 193097.2140438	test: 189546.0780496	best: 189546.0780496 (1)	total: 156ms	remaining: 1m 18s
2:	learn: 188112.2883838	test: 184530.8663171	best: 184530.8663171 (2)	total: 164ms	remaining: 54.5s
3:	learn: 183192.0753443	test: 179462.5063936	best: 179462.5063936 (3)	total: 172ms	remaining: 42.8s
4:	learn: 178405.6789454	test: 174505.4214737	best: 174505.4214737 (4)	total: 180ms	remaining: 35.8s
5:	learn: 173921.9608047	test: 169838.6495223	best: 169838.6495223 (5)	total: 188ms	remaining: 31.1s
6:	learn: 169521.5962738	test: 165318.5386872	best: 165318.5386872 (6)	total: 196ms	remaining: 27.8s
7:	learn: 165232.5238371	test: 160946.0802664	best: 160946.0802664 (7)	total: 204ms	remaining: 25.3s
8:	learn: 161041.8415815	test: 156725.1303760	best: 156725.1303760 (8)	total: 209ms	remaining: 23s
9:	learn: 157090.2520134	test: 152658.7561098	best: 152658.7561098 (9)	total: 216ms	remaini

83:	learn: 40369.5108337	test: 38804.0432908	best: 38804.0432908 (83)	total: 772ms	remaining: 8.42s
84:	learn: 40047.2853155	test: 38617.2691857	best: 38617.2691857 (84)	total: 781ms	remaining: 8.41s
85:	learn: 39616.7813334	test: 38326.9365265	best: 38326.9365265 (85)	total: 789ms	remaining: 8.39s
86:	learn: 39317.2284615	test: 38186.8662980	best: 38186.8662980 (86)	total: 797ms	remaining: 8.36s
87:	learn: 39071.7876198	test: 37996.7891493	best: 37996.7891493 (87)	total: 804ms	remaining: 8.34s
88:	learn: 38731.7286606	test: 37812.9953989	best: 37812.9953989 (88)	total: 811ms	remaining: 8.3s
89:	learn: 38373.8780748	test: 37642.4657604	best: 37642.4657604 (89)	total: 819ms	remaining: 8.28s
90:	learn: 38101.9159199	test: 37481.7173799	best: 37481.7173799 (90)	total: 826ms	remaining: 8.25s
91:	learn: 37795.1217529	test: 37267.5592527	best: 37267.5592527 (91)	total: 834ms	remaining: 8.23s
92:	learn: 37482.2750717	test: 37209.4621866	best: 37209.4621866 (92)	total: 841ms	remaining: 8.2s
93

188:	learn: 26680.4031832	test: 36202.1675949	best: 35648.5621319 (154)	total: 1.59s	remaining: 6.84s
189:	learn: 26600.9183121	test: 36172.5983381	best: 35648.5621319 (154)	total: 1.6s	remaining: 6.83s
190:	learn: 26546.2892146	test: 36153.1955570	best: 35648.5621319 (154)	total: 1.61s	remaining: 6.82s
191:	learn: 26473.6351394	test: 36251.3948418	best: 35648.5621319 (154)	total: 1.62s	remaining: 6.81s
192:	learn: 26401.7913687	test: 36301.8265320	best: 35648.5621319 (154)	total: 1.63s	remaining: 6.8s
193:	learn: 26357.4500166	test: 36336.8518442	best: 35648.5621319 (154)	total: 1.63s	remaining: 6.79s
194:	learn: 26333.6924544	test: 36367.5675428	best: 35648.5621319 (154)	total: 1.64s	remaining: 6.78s
195:	learn: 26294.6145801	test: 36432.8822443	best: 35648.5621319 (154)	total: 1.65s	remaining: 6.76s
196:	learn: 26249.2048635	test: 36486.1826985	best: 35648.5621319 (154)	total: 1.66s	remaining: 6.75s
197:	learn: 26238.5226438	test: 36488.9633529	best: 35648.5621319 (154)	total: 1.66s

270:	learn: 23604.5794725	test: 37549.2456311	best: 35648.5621319 (154)	total: 2.22s	remaining: 5.97s
271:	learn: 23604.3257767	test: 37546.0515608	best: 35648.5621319 (154)	total: 2.23s	remaining: 5.96s
272:	learn: 23566.3125906	test: 37602.8635709	best: 35648.5621319 (154)	total: 2.23s	remaining: 5.95s
273:	learn: 23530.8078635	test: 37603.3130361	best: 35648.5621319 (154)	total: 2.24s	remaining: 5.94s
274:	learn: 23494.4138477	test: 37589.5268904	best: 35648.5621319 (154)	total: 2.25s	remaining: 5.93s
275:	learn: 23475.7804070	test: 37637.8877391	best: 35648.5621319 (154)	total: 2.26s	remaining: 5.92s
276:	learn: 23452.7546596	test: 37643.8035380	best: 35648.5621319 (154)	total: 2.26s	remaining: 5.91s
277:	learn: 23434.4160045	test: 37694.2457549	best: 35648.5621319 (154)	total: 2.27s	remaining: 5.9s
278:	learn: 23414.2539788	test: 37717.6083949	best: 35648.5621319 (154)	total: 2.28s	remaining: 5.89s
279:	learn: 23402.1807085	test: 37758.4767464	best: 35648.5621319 (154)	total: 2.29

353:	learn: 21515.7354483	test: 38087.1990650	best: 35648.5621319 (154)	total: 2.86s	remaining: 5.23s
354:	learn: 21496.7968780	test: 38119.3868442	best: 35648.5621319 (154)	total: 2.87s	remaining: 5.22s
355:	learn: 21481.1909787	test: 38157.7125645	best: 35648.5621319 (154)	total: 2.88s	remaining: 5.21s
356:	learn: 21467.1965401	test: 38161.9342428	best: 35648.5621319 (154)	total: 2.89s	remaining: 5.21s
357:	learn: 21456.6990449	test: 38176.3454845	best: 35648.5621319 (154)	total: 2.9s	remaining: 5.2s
358:	learn: 21419.3122908	test: 38179.9866921	best: 35648.5621319 (154)	total: 2.91s	remaining: 5.19s
359:	learn: 21407.1063110	test: 38179.7698862	best: 35648.5621319 (154)	total: 2.91s	remaining: 5.18s
360:	learn: 21392.1807358	test: 38217.2557943	best: 35648.5621319 (154)	total: 2.92s	remaining: 5.17s
361:	learn: 21391.9592823	test: 38213.4415195	best: 35648.5621319 (154)	total: 2.93s	remaining: 5.16s
362:	learn: 21378.4230326	test: 38212.1249724	best: 35648.5621319 (154)	total: 2.94s

...

2752:	learn: 893.4322627	test: 32622.9797383	best: 32620.3286091 (2653)	total: 4m 8s	remaining: 22.3s
2753:	learn: 892.4940825	test: 32622.1992688	best: 32620.3286091 (2653)	total: 4m 8s	remaining: 22.2s
2754:	learn: 891.7764391	test: 32622.4163583	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 22.1s
2755:	learn: 891.7596867	test: 32622.4422422	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 22.1s
2756:	learn: 891.2105545	test: 32622.4854204	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 22s
2757:	learn: 890.2638318	test: 32622.3964044	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 21.9s
2758:	learn: 889.1711456	test: 32622.5185353	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 21.8s
2759:	learn: 889.0921118	test: 32622.4444895	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 21.7s
2760:	learn: 887.3695396	test: 32622.2984486	best: 32620.3286091 (2653)	total: 4m 9s	remaining: 21.6s
2761:	learn: 886.1885203	test: 32623.0830346	best: 32620.3286091 (2653)	total: 4m 9s

2832:	learn: 839.5779036	test: 32626.2376579	best: 32620.3286091 (2653)	total: 4m 16s	remaining: 15.1s
2833:	learn: 838.6452048	test: 32626.1277627	best: 32620.3286091 (2653)	total: 4m 16s	remaining: 15s
2834:	learn: 837.4941200	test: 32625.9539669	best: 32620.3286091 (2653)	total: 4m 16s	remaining: 14.9s
2835:	learn: 836.5569952	test: 32626.1173043	best: 32620.3286091 (2653)	total: 4m 16s	remaining: 14.8s
2836:	learn: 836.1119000	test: 32625.9096141	best: 32620.3286091 (2653)	total: 4m 16s	remaining: 14.8s
2837:	learn: 835.2933783	test: 32625.9116399	best: 32620.3286091 (2653)	total: 4m 17s	remaining: 14.7s
2838:	learn: 834.5434974	test: 32626.0062318	best: 32620.3286091 (2653)	total: 4m 17s	remaining: 14.6s
2839:	learn: 833.8482240	test: 32625.9583540	best: 32620.3286091 (2653)	total: 4m 17s	remaining: 14.5s
2840:	learn: 833.3111361	test: 32626.0478221	best: 32620.3286091 (2653)	total: 4m 17s	remaining: 14.4s
2841:	learn: 833.1016876	test: 32626.3030132	best: 32620.3286091 (2653)	tot

2913:	learn: 781.8343104	test: 32625.1262302	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.79s
2914:	learn: 780.2047323	test: 32624.9513053	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.7s
2915:	learn: 779.1039177	test: 32625.1988460	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.61s
2916:	learn: 777.5360275	test: 32625.1285686	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.52s
2917:	learn: 777.3890390	test: 32625.4883485	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.43s
2918:	learn: 776.2094731	test: 32625.5342782	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.34s
2919:	learn: 776.0507347	test: 32625.5522747	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.25s
2920:	learn: 775.1405070	test: 32625.5365169	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.16s
2921:	learn: 775.0650593	test: 32625.4579522	best: 32620.3286091 (2653)	total: 4m 24s	remaining: 7.07s
2922:	learn: 774.3843853	test: 32625.4230081	best: 32620.3286091 (2653)	to

2995:	learn: 723.0915105	test: 32625.1509732	best: 32620.3286091 (2653)	total: 4m 31s	remaining: 363ms
2996:	learn: 721.6079232	test: 32624.8626974	best: 32620.3286091 (2653)	total: 4m 31s	remaining: 272ms
2997:	learn: 721.0484364	test: 32624.8916529	best: 32620.3286091 (2653)	total: 4m 31s	remaining: 181ms
2998:	learn: 720.3416281	test: 32624.9785353	best: 32620.3286091 (2653)	total: 4m 32s	remaining: 90.7ms
2999:	learn: 719.9101897	test: 32624.6642181	best: 32620.3286091 (2653)	total: 4m 32s	remaining: 0us

bestTest = 32620.32861
bestIteration = 2653



{'params': {'depth': 9, 'iterations': 3000},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               45,
               46,
               47,
      

In [122]:
catboost.get_params()

{'loss_function': 'RMSE',
 'eval_metric': 'RMSE',
 'cat_features': ['MSSubClass',
  'OverallQual',
  'OverallCond',
  'BsmtFullBath',
  'BsmtHalfBath',
  'FullBath',
  'HalfBath',
  'BedroomAbvGr',
  'KitchenAbvGr',
  'TotRmsAbvGrd',
  'Fireplaces',
  'GarageCars',
  'MoSold',
  'YrSold',
  'MSZoning',
  'LotShape',
  'LandContour',
  'LotConfig',
  'LandSlope',
  'Neighborhood',
  'Condition1',
  'BldgType',
  'HouseStyle',
  'RoofStyle',
  'Exterior1st',
  'Exterior2nd',
  'MasVnrType',
  'ExterQual',
  'ExterCond',
  'Foundation',
  'BsmtQual',
  'BsmtCond',
  'BsmtExposure',
  'BsmtFinType1',
  'BsmtFinType2',
  'HeatingQC',
  'CentralAir',
  'Electrical',
  'KitchenQual',
  'Functional',
  'FireplaceQu',
  'GarageType',
  'GarageFinish',
  'GarageQual',
  'PavedDrive',
  'SaleType',
  'SaleCondition'],
 'depth': 9,
 'iterations': 3000}

In [180]:
catboost = CatBoostRegressor(cat_features=cat_cols, eval_metric='RMSE', loss_function='RMSE',
                             iterations=5000, max_depth=8)
catboost.fit(df, y)

Learning rate set to 0.0116
0:	learn: 78438.4103709	total: 34.9ms	remaining: 2m 54s
1:	learn: 77908.5100723	total: 78.9ms	remaining: 3m 17s
2:	learn: 77351.0778977	total: 130ms	remaining: 3m 36s
3:	learn: 76827.3268309	total: 174ms	remaining: 3m 37s
4:	learn: 76283.1681864	total: 219ms	remaining: 3m 38s
5:	learn: 75735.0718973	total: 250ms	remaining: 3m 28s
6:	learn: 75209.6926344	total: 289ms	remaining: 3m 25s
7:	learn: 74690.8873976	total: 334ms	remaining: 3m 28s
8:	learn: 74182.8310295	total: 377ms	remaining: 3m 29s
9:	learn: 73657.0147446	total: 422ms	remaining: 3m 30s
10:	learn: 73114.4770157	total: 469ms	remaining: 3m 32s
11:	learn: 72592.2748882	total: 517ms	remaining: 3m 34s
12:	learn: 72075.2352205	total: 560ms	remaining: 3m 34s
13:	learn: 71597.1692947	total: 594ms	remaining: 3m 31s
14:	learn: 71113.1863050	total: 638ms	remaining: 3m 32s
15:	learn: 70660.6531590	total: 667ms	remaining: 3m 27s
16:	learn: 70163.2137291	total: 705ms	remaining: 3m 26s
17:	learn: 69715.6972626	tot

147:	learn: 35778.5841521	total: 6.56s	remaining: 3m 34s
148:	learn: 35643.8304338	total: 6.6s	remaining: 3m 34s
149:	learn: 35517.2614293	total: 6.64s	remaining: 3m 34s
150:	learn: 35405.6996107	total: 6.69s	remaining: 3m 34s
151:	learn: 35305.4772247	total: 6.74s	remaining: 3m 35s
152:	learn: 35166.7881948	total: 6.79s	remaining: 3m 35s
153:	learn: 35029.9488782	total: 6.84s	remaining: 3m 35s
154:	learn: 34888.9420086	total: 6.89s	remaining: 3m 35s
155:	learn: 34747.9296530	total: 6.94s	remaining: 3m 35s
156:	learn: 34632.0398989	total: 6.96s	remaining: 3m 34s
157:	learn: 34497.6363144	total: 7.01s	remaining: 3m 34s
158:	learn: 34369.9251318	total: 7.06s	remaining: 3m 34s
159:	learn: 34241.5608250	total: 7.11s	remaining: 3m 35s
160:	learn: 34129.4714136	total: 7.16s	remaining: 3m 35s
161:	learn: 33999.8355779	total: 7.2s	remaining: 3m 35s
162:	learn: 33899.8005043	total: 7.25s	remaining: 3m 35s
163:	learn: 33783.1349386	total: 7.29s	remaining: 3m 35s
164:	learn: 33669.9595520	total: 

293:	learn: 24385.2050716	total: 13.5s	remaining: 3m 35s
294:	learn: 24347.7164460	total: 13.5s	remaining: 3m 35s
295:	learn: 24298.2569978	total: 13.6s	remaining: 3m 35s
296:	learn: 24250.0716860	total: 13.6s	remaining: 3m 35s
297:	learn: 24208.4616690	total: 13.7s	remaining: 3m 35s
298:	learn: 24171.2995861	total: 13.7s	remaining: 3m 36s
299:	learn: 24141.1683365	total: 13.8s	remaining: 3m 36s
300:	learn: 24108.2355038	total: 13.8s	remaining: 3m 36s
301:	learn: 24065.5233245	total: 13.9s	remaining: 3m 36s
302:	learn: 24035.2711478	total: 13.9s	remaining: 3m 36s
303:	learn: 23983.2336612	total: 14s	remaining: 3m 35s
304:	learn: 23948.1675047	total: 14s	remaining: 3m 35s
305:	learn: 23909.4752702	total: 14.1s	remaining: 3m 36s
306:	learn: 23859.8847697	total: 14.1s	remaining: 3m 36s
307:	learn: 23823.4126786	total: 14.2s	remaining: 3m 36s
308:	learn: 23777.8599487	total: 14.2s	remaining: 3m 36s
309:	learn: 23741.7229060	total: 14.3s	remaining: 3m 36s
310:	learn: 23703.3896769	total: 14

442:	learn: 19763.9291349	total: 20.7s	remaining: 3m 33s
443:	learn: 19745.2841376	total: 20.8s	remaining: 3m 33s
444:	learn: 19726.2044114	total: 20.8s	remaining: 3m 33s
445:	learn: 19714.8459434	total: 20.9s	remaining: 3m 33s
446:	learn: 19694.2476722	total: 20.9s	remaining: 3m 33s
447:	learn: 19672.6055000	total: 21s	remaining: 3m 33s
448:	learn: 19647.3118165	total: 21.1s	remaining: 3m 33s
449:	learn: 19622.2566858	total: 21.1s	remaining: 3m 33s
450:	learn: 19598.2249394	total: 21.2s	remaining: 3m 33s
451:	learn: 19566.3000734	total: 21.2s	remaining: 3m 33s
452:	learn: 19538.6339895	total: 21.3s	remaining: 3m 33s
453:	learn: 19513.9695723	total: 21.3s	remaining: 3m 33s
454:	learn: 19488.2914892	total: 21.4s	remaining: 3m 33s
455:	learn: 19465.4086724	total: 21.4s	remaining: 3m 33s
456:	learn: 19442.7955008	total: 21.5s	remaining: 3m 33s
457:	learn: 19427.3927371	total: 21.5s	remaining: 3m 33s
458:	learn: 19408.8596995	total: 21.5s	remaining: 3m 33s
459:	learn: 19387.3428225	total: 

588:	learn: 17117.6484118	total: 27.8s	remaining: 3m 27s
589:	learn: 17108.4807145	total: 27.8s	remaining: 3m 27s
590:	learn: 17091.3932643	total: 27.9s	remaining: 3m 27s
591:	learn: 17086.5516192	total: 27.9s	remaining: 3m 27s
592:	learn: 17069.8171391	total: 27.9s	remaining: 3m 27s
593:	learn: 17058.8809281	total: 27.9s	remaining: 3m 27s
594:	learn: 17038.4576733	total: 28s	remaining: 3m 27s
595:	learn: 17028.7654264	total: 28.1s	remaining: 3m 27s
596:	learn: 17018.0052672	total: 28.1s	remaining: 3m 27s
597:	learn: 16998.7249675	total: 28.1s	remaining: 3m 27s
598:	learn: 16985.3705065	total: 28.2s	remaining: 3m 27s
599:	learn: 16972.8613783	total: 28.3s	remaining: 3m 27s
600:	learn: 16956.2132646	total: 28.3s	remaining: 3m 27s
601:	learn: 16947.4074975	total: 28.4s	remaining: 3m 27s
602:	learn: 16933.4064835	total: 28.4s	remaining: 3m 27s
603:	learn: 16914.8576835	total: 28.5s	remaining: 3m 27s
604:	learn: 16899.0820455	total: 28.5s	remaining: 3m 27s
605:	learn: 16889.0610136	total: 

...

4384:	learn: 3893.0807498	total: 3m 32s	remaining: 29.8s
4385:	learn: 3891.4976237	total: 3m 32s	remaining: 29.8s
4386:	learn: 3890.2121180	total: 3m 32s	remaining: 29.7s
4387:	learn: 3889.6146810	total: 3m 32s	remaining: 29.7s
4388:	learn: 3888.4701187	total: 3m 32s	remaining: 29.6s
4389:	learn: 3885.9819830	total: 3m 32s	remaining: 29.6s
4390:	learn: 3885.5918055	total: 3m 32s	remaining: 29.5s
4391:	learn: 3883.1578111	total: 3m 32s	remaining: 29.5s
4392:	learn: 3882.9578394	total: 3m 32s	remaining: 29.4s
4393:	learn: 3880.4277118	total: 3m 32s	remaining: 29.4s
4394:	learn: 3878.7939597	total: 3m 33s	remaining: 29.3s
4395:	learn: 3877.9822982	total: 3m 33s	remaining: 29.3s
4396:	learn: 3877.9431003	total: 3m 33s	remaining: 29.2s
4397:	learn: 3877.2049641	total: 3m 33s	remaining: 29.2s
4398:	learn: 3876.9563224	total: 3m 33s	remaining: 29.1s
4399:	learn: 3875.5743910	total: 3m 33s	remaining: 29.1s
4400:	learn: 3874.7108437	total: 3m 33s	remaining: 29s
4401:	learn: 3872.5737948	total: 

4531:	learn: 3741.5065709	total: 3m 39s	remaining: 22.7s
4532:	learn: 3739.7635212	total: 3m 40s	remaining: 22.7s
4533:	learn: 3738.8368496	total: 3m 40s	remaining: 22.6s
4534:	learn: 3737.3348977	total: 3m 40s	remaining: 22.6s
4535:	learn: 3737.0698858	total: 3m 40s	remaining: 22.5s
4536:	learn: 3736.0746795	total: 3m 40s	remaining: 22.5s
4537:	learn: 3735.9555835	total: 3m 40s	remaining: 22.4s
4538:	learn: 3735.7402424	total: 3m 40s	remaining: 22.4s
4539:	learn: 3735.2106080	total: 3m 40s	remaining: 22.3s
4540:	learn: 3733.6348539	total: 3m 40s	remaining: 22.3s
4541:	learn: 3732.3661299	total: 3m 40s	remaining: 22.2s
4542:	learn: 3731.2110881	total: 3m 40s	remaining: 22.2s
4543:	learn: 3731.1821072	total: 3m 40s	remaining: 22.1s
4544:	learn: 3730.7083294	total: 3m 40s	remaining: 22.1s
4545:	learn: 3730.6293293	total: 3m 40s	remaining: 22s
4546:	learn: 3728.5591521	total: 3m 40s	remaining: 22s
4547:	learn: 3727.3418182	total: 3m 40s	remaining: 21.9s
4548:	learn: 3725.9133214	total: 3m

4678:	learn: 3596.6449793	total: 3m 47s	remaining: 15.6s
4679:	learn: 3595.0928060	total: 3m 47s	remaining: 15.5s
4680:	learn: 3594.9174518	total: 3m 47s	remaining: 15.5s
4681:	learn: 3593.7759514	total: 3m 47s	remaining: 15.5s
4682:	learn: 3592.6193231	total: 3m 47s	remaining: 15.4s
4683:	learn: 3591.5390717	total: 3m 47s	remaining: 15.4s
4684:	learn: 3590.3881750	total: 3m 47s	remaining: 15.3s
4685:	learn: 3590.3573242	total: 3m 47s	remaining: 15.3s
4686:	learn: 3589.5713354	total: 3m 47s	remaining: 15.2s
4687:	learn: 3589.0900947	total: 3m 47s	remaining: 15.2s
4688:	learn: 3588.8926664	total: 3m 47s	remaining: 15.1s
4689:	learn: 3588.5484080	total: 3m 47s	remaining: 15.1s
4690:	learn: 3588.2493820	total: 3m 47s	remaining: 15s
4691:	learn: 3588.0357641	total: 3m 48s	remaining: 15s
4692:	learn: 3585.8148992	total: 3m 48s	remaining: 14.9s
4693:	learn: 3584.3457517	total: 3m 48s	remaining: 14.9s
4694:	learn: 3583.1370608	total: 3m 48s	remaining: 14.8s
4695:	learn: 3581.0645787	total: 3m

4826:	learn: 3464.3917652	total: 3m 54s	remaining: 8.41s
4827:	learn: 3463.4279493	total: 3m 54s	remaining: 8.36s
4828:	learn: 3462.3089842	total: 3m 54s	remaining: 8.31s
4829:	learn: 3461.2400181	total: 3m 54s	remaining: 8.26s
4830:	learn: 3460.3933426	total: 3m 54s	remaining: 8.21s
4831:	learn: 3459.8446388	total: 3m 54s	remaining: 8.17s
4832:	learn: 3458.9100061	total: 3m 54s	remaining: 8.12s
4833:	learn: 3456.5936284	total: 3m 54s	remaining: 8.07s
4834:	learn: 3456.3390144	total: 3m 55s	remaining: 8.02s
4835:	learn: 3454.9567862	total: 3m 55s	remaining: 7.97s
4836:	learn: 3453.2458819	total: 3m 55s	remaining: 7.92s
4837:	learn: 3452.3406437	total: 3m 55s	remaining: 7.88s
4838:	learn: 3450.4024545	total: 3m 55s	remaining: 7.83s
4839:	learn: 3449.3863110	total: 3m 55s	remaining: 7.78s
4840:	learn: 3448.3084694	total: 3m 55s	remaining: 7.73s
4841:	learn: 3447.7828155	total: 3m 55s	remaining: 7.68s
4842:	learn: 3447.5166859	total: 3m 55s	remaining: 7.63s
4843:	learn: 3446.8126639	total

4976:	learn: 3328.9970371	total: 4m 2s	remaining: 1.12s
4977:	learn: 3327.3856479	total: 4m 2s	remaining: 1.07s
4978:	learn: 3326.4201999	total: 4m 2s	remaining: 1.02s
4979:	learn: 3325.0899153	total: 4m 2s	remaining: 973ms
4980:	learn: 3323.3523419	total: 4m 2s	remaining: 924ms
4981:	learn: 3323.3212777	total: 4m 2s	remaining: 875ms
4982:	learn: 3322.7677541	total: 4m 2s	remaining: 827ms
4983:	learn: 3322.1248682	total: 4m 2s	remaining: 778ms
4984:	learn: 3321.2874363	total: 4m 2s	remaining: 729ms
4985:	learn: 3321.0644289	total: 4m 2s	remaining: 681ms
4986:	learn: 3320.2310002	total: 4m 2s	remaining: 632ms
4987:	learn: 3319.5488774	total: 4m 2s	remaining: 584ms
4988:	learn: 3319.4152081	total: 4m 2s	remaining: 535ms
4989:	learn: 3319.3527216	total: 4m 2s	remaining: 486ms
4990:	learn: 3318.1694652	total: 4m 2s	remaining: 438ms
4991:	learn: 3317.0582862	total: 4m 2s	remaining: 389ms
4992:	learn: 3315.9434468	total: 4m 2s	remaining: 340ms
4993:	learn: 3315.8592483	total: 4m 2s	remaining

In [181]:
y_pred_boost = catboost.predict(X_test_boost)

In [182]:
np.sqrt(mean_squared_error(y_test_boost, y_pred_boost))

8384.060442101085

## TEST

In [235]:
data_test = pd.read_csv('C:/Users/markc/Downloads/houses/test.csv')

**Удаляем ненужные колонки**

In [236]:
data_test.drop(['PoolQC', 'MiscFeature', 'Alley', 'Fence', 'Street', 'Utilities', 'Condition2', 'RoofMatl', 'Heating', 
         'GarageCond', '3SsnPorch', 'ScreenPorch', 'BsmtFinSF2', 'LowQualFinSF', 'PoolArea', 'MiscVal'], 
        axis=1, inplace=True)

**Заполняем NaN-ы**

In [237]:
data_test.loc[data_test.MSZoning.isna(), 'MSZoning'] = data_test[(data_test.MSZoning.notna()) & 
                                                                 (df.MSSubClass == 20)].MSZoning.value_counts().index[0]

In [238]:
data_test.loc[data_test.Exterior1st.isna(), 'Exterior1st'] = data_test[data_test.Exterior1st.notna()].Exterior1st.value_counts().index[0]
data_test.loc[data_test.Exterior2nd.isna(), 'Exterior2nd'] = data_test[data_test.Exterior2nd.notna()].Exterior2nd.value_counts().index[0]

In [239]:
data_test.loc[data_test.MasVnrType.isna(), 'MasVnrType'] = data_test[data_test.Foundation == 'PConc'].MasVnrType.value_counts().index[1]

In [240]:
data_test.loc[data_test.MasVnrArea.isna(), 'MasVnrArea'] = data_test[(data_test.OverallCond == 5) & 
                                                                     (data_test.RoofStyle == 'Gable') & 
                                                                     (data_test.ExterQual == 'TA') & 
                                                                     (data_test.ExterCond == 'TA') & 
                                                                     (data_test.Foundation == 'PConc') & 
                                                                     (data_test.BsmtQual == 'TA') & 
                                                                     (data_test.BsmtCond == 'TA') & 
                                                                     (data_test.BsmtExposure == 'No')].MasVnrArea.mean()

In [241]:
data_test.loc[data_test.KitchenQual.isna(), 'KitchenQual'] = data_test[(data_test.KitchenQual.notna()) & 
                                                                       (data_test.KitchenAbvGr == 1) & 
                                                                       (data_test.OverallQual == 5)].KitchenQual.value_counts().index[0]

In [242]:
data_test[data_test.Functional.notna()].groupby(['Functional']).YearBuilt.describe()

count         mean        std     min      25%     50%      75%  \
Functional                                                                     
Maj1           5.0  1945.800000  44.024993  1900.0  1920.00  1925.0  1980.00   
Maj2           4.0  1948.500000   7.371115  1939.0  1946.50  1949.0  1951.00   
Min1          34.0  1952.735294  18.787986  1910.0  1945.50  1953.5  1961.75   
Min2          36.0  1949.222222  24.516014  1900.0  1933.75  1950.5  1962.50   
Mod           20.0  1946.100000  26.865944  1880.0  1925.00  1947.5  1961.75   
Sev            1.0  1922.000000        NaN  1922.0  1922.00  1922.0  1922.00   
Typ         1357.0  1973.041268  30.169918  1879.0  1955.00  1976.0  2002.00   

               max  
Functional          
Maj1        2004.0  
Maj2        1957.0  
Min1        1997.0  
Min2        2004.0  
Mod         2004.0  
Sev         1922.0  
Typ         2010.0

In [243]:
data_test[data_test.Functional.isna()].YearBuilt

756     1952
1013    1910
Name: YearBuilt, dtype: int64

In [244]:
data_test.loc[(data_test.Functional.isna()) & (data_test.YearBuilt < 1922), 'Functional'] = 'Sev'
data_test.loc[(data_test.Functional.isna()) & (data_test.YearBuilt == 1952), 'Functional'] = 'Min1'

In [245]:
data_test[data_test.GarageCars.notna()].groupby('GarageCars').GarageArea.mean()

GarageCars
0.0       0.000000
1.0     299.931204
2.0     519.042857
3.0     805.284974
4.0     996.181818
5.0    1184.000000
Name: GarageArea, dtype: float64

In [246]:
data_test.loc[data_test.GarageCars.isna(), 'GarageCars'] = 3
data_test.loc[data_test.GarageArea.isna(), 'GarageArea'] = 805.284974

In [247]:
data_test[data_test.SaleType.notna()].groupby(['SaleType']).YearBuilt.describe()

count         mean        std     min      25%     50%      75%  \
SaleType                                                                     
COD         44.0  1953.204545  22.637260  1900.0  1946.25  1960.5  1966.25   
CWD          8.0  1965.375000  27.171085  1921.0  1955.50  1967.0  1974.50   
Con          3.0  1974.666667  34.501208  1940.0  1957.50  1975.0  1992.00   
ConLD       17.0  1952.294118  32.459137  1910.0  1920.00  1953.0  1971.00   
ConLI        4.0  1947.000000  40.938979  1920.0  1927.50  1930.0  1949.50   
ConLw        3.0  1922.333333  20.744477  1900.0  1913.00  1926.0  1933.50   
New        117.0  2006.427350   1.124310  2004.0  2006.00  2006.0  2007.00   
Oth          4.0  1950.250000  20.694202  1920.0  1945.50  1958.0  1962.75   
WD        1258.0  1969.290938  29.729268  1879.0  1952.00  1971.0  1998.00   

             max  
SaleType          
COD       1999.0  
CWD       2006.0  
Con       2009.0  
ConLD     2004.0  
ConLI     2008.0  
ConLw     1941.0  
New       2010.0  
Oth       1965.0  
WD        2010.0

In [248]:
data_test.loc[data_test.SaleType.isna(), 'SaleType'] = 'COD'

In [249]:
data_test.loc[(data_test.BsmtFullBath.isna()) & (data_test.BsmtFinSF1 == 0), 'BsmtFullBath'] = 0

In [250]:
data_test.loc[data_test.BsmtCond.isna(), 'BsmtCond'] = data_test[data_test.BsmtCond.notna()].BsmtCond.value_counts().index[0]

In [251]:
data_test[(data_test.BsmtQual.notna()) & (data_test.OverallQual == 5) & (data_test.ExterQual == 'TA') & (data_test.KitchenQual == 'TA')].BsmtQual.value_counts()

TA    224
Gd     70
Fa     13
Name: BsmtQual, dtype: int64

In [252]:
data_test.loc[data_test.BsmtQual.isna(), 'BsmtQual'] = 'TA'

In [253]:
data_test[data_test.BsmtExposure.notna()].groupby(['BsmtExposure']).BsmtQual.value_counts()

BsmtExposure  BsmtQual
Av            Gd          126
              TA           44
              Ex           27
Gd            Gd           70
              Ex           57
              TA           14
              Fa            1
Mn            Gd           58
              TA           51
              Ex           11
              Fa            5
No            TA          527
              Gd          335
              Fa           47
              Ex           42
Name: BsmtQual, dtype: int64

In [254]:
data_test.loc[data_test.BsmtExposure.isna(), 'BsmtExposure'] = 'No'

In [255]:
data_test[data_test.BsmtFinType2.notna()].groupby('BsmtFinType2').BsmtFinSF1.describe()

count        mean         std   min     25%    50%    75%  \
BsmtFinType2                                                               
ALQ             33.0  350.606061  298.308768  53.0  114.00  242.0  475.0   
BLQ             35.0  443.257143  385.782653  60.0  135.00  380.0  670.0   
GLQ             20.0  205.850000  133.877114  16.0  105.75  226.0  266.5   
LwQ             41.0  551.073171  345.359044  20.0  299.00  510.0  687.0   
Rec             51.0  511.686275  372.330847  32.0  250.50  468.0  646.0   
Unf           1237.0  453.086500  468.906263   0.0    0.00  375.0  776.0   

                 max  
BsmtFinType2          
ALQ           1252.0  
BLQ           1728.0  
GLQ            560.0  
LwQ           1593.0  
Rec           1733.0  
Unf           4010.0

In [256]:
data_test[data_test.BsmtFinType2.isna()].BsmtFinSF1.mean()

0.0

In [257]:
data_test.loc[data_test.BsmtFinType1.isna(), 'BsmtFinType1'] = 'Unf'
data_test.loc[data_test.BsmtFinType2.isna(), 'BsmtFinType2'] = 'Unf'

In [258]:
data_test.loc[data_test.BsmtFinSF1.isna(), 'BsmtFinSF1'] = 0

In [259]:
data_test.TotalBsmtSF.describe()

count    1458.000000
mean     1046.117970
std       442.898624
min         0.000000
25%       784.000000
50%       988.000000
75%      1305.000000
max      5095.000000
Name: TotalBsmtSF, dtype: float64

In [260]:
data_test['1stFlrSF'].describe()

count    1459.000000
mean     1156.534613
std       398.165820
min       407.000000
25%       873.500000
50%      1079.000000
75%      1382.500000
max      5095.000000
Name: 1stFlrSF, dtype: float64

In [261]:
data_test.loc[data_test.TotalBsmtSF.isna(), 'TotalBsmtSF'] = 780
data_test.loc[data_test.BsmtUnfSF.isna(), 'BsmtUnfSF'] = 780

In [262]:
data_test.loc[data_test.BsmtFullBath.isna(), 'BsmtFullBath'] = 1
data_test.loc[data_test.BsmtHalfBath.isna(), 'BsmtHalfBath'] = 0

In [263]:
data_test[data_test.GarageYrBlt.notna()][(data_test.YearBuilt > 1890) & (data_test.YearBuilt < 1950)].GarageYrBlt.describe()

C:\Users\markc\AppData\Local\Temp\ipykernel_14712\3972240486.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  data_test[data_test.GarageYrBlt.notna()][(data_test.YearBuilt > 1890) & (data_test.YearBuilt < 1950)].GarageYrBlt.describe()


count     266.000000
mean     1945.428571
std        25.098684
min      1895.000000
25%      1926.000000
50%      1940.000000
75%      1959.750000
max      2008.000000
Name: GarageYrBlt, dtype: float64

In [264]:
data_test.loc[data_test.GarageType.isna(), 'GarageType'] = 'NA'

In [265]:
data_test.loc[data_test.GarageYrBlt.isna() & (data_test.GarageType == 'NA'), 'GarageYrBlt'] = 1895
data_test.loc[(data_test.GarageQual.isna()) & (data_test.GarageType == 'NA'), 'GarageQual'] = 'NA'
data_test.loc[data_test.GarageFinish.isna() & (data_test.GarageType == 'NA'), 'GarageFinish'] = 'NA'

In [266]:
data_test.GarageYrBlt.describe()

count    1457.000000
mean     1973.406314
std        31.633672
min      1895.000000
25%      1956.000000
50%      1977.000000
75%      2001.000000
max      2207.000000
Name: GarageYrBlt, dtype: float64

In [267]:
data_test[data_test.GarageYrBlt.notna()].YearBuilt.describe()

count    1457.000000
mean     1971.433082
std        30.341845
min      1879.000000
25%      1953.000000
50%      1973.000000
75%      2001.000000
max      2010.000000
Name: YearBuilt, dtype: float64

In [268]:
data_test.loc[(data_test.GarageYrBlt.isna()) & (data_test.YearBuilt == 1910), 'GarageYrBlt'] = 1910
data_test.loc[(data_test.GarageYrBlt.isna()) & (data_test.YearBuilt == 1923), 'GarageYrBlt'] = 1923

In [269]:
data_test.loc[data_test.GarageQual.isna(), 'GarageQual'] = 'Fa'

In [270]:
data_test.loc[data_test.GarageFinish.isna(),'GarageFinish'] = 'Unf'

In [271]:
data_test.loc[data_test['LotFrontage'].isna(), 'LotFrontage'] = data_test[(data_test.LotFrontage.notna()) & 
                                                                          (data_test.LotShape == 'Reg') & 
                                                                          (data_test.LotConfig == 'Inside')].LotFrontage.mean() + 1

In [272]:
data_test[data_test.FireplaceQu.notna()].groupby(data_test.FireplaceQu)['1stFlrSF'].describe()

count         mean         std    min     25%     50%      75%  \
FireplaceQu                                                                   
Ex            19.0  1708.157895  481.757346  960.0  1423.0  1688.0  1979.00   
Fa            41.0  1172.317073  283.489368  765.0  1008.0  1083.0  1324.00   
Gd           364.0  1377.502747  493.816617  565.0  1012.5  1358.0  1651.25   
Po            26.0  1078.307692  257.872491  502.0   942.0  1060.5  1277.00   
TA           279.0  1210.584229  323.492407  516.0   952.0  1191.0  1446.00   

                max  
FireplaceQu          
Ex           2552.0  
Fa           2064.0  
Gd           5095.0  
Po           1576.0  
TA           2362.0

In [273]:
data_test.loc[(data_test.FireplaceQu.isna()) & (data_test['1stFlrSF'] >= 1720) , 'FireplaceQu'] = 'Ex'
data_test.loc[(data_test.FireplaceQu.isna()) & (data_test['1stFlrSF'] >= 1400) & (data_test['1stFlrSF'] < 1720), 
              'FireplaceQu'] = 'Gd'
data_test.loc[(data_test.FireplaceQu.isna()) & (data_test['1stFlrSF'] >= 1200) & (data_test['1stFlrSF'] < 1400), 
              'FireplaceQu'] = 'TA'
data_test.loc[(data_test.FireplaceQu.isna()) & (data_test['1stFlrSF'] >= 1060) & (data_test['1stFlrSF'] < 1200), 
              'FireplaceQu'] = 'Fa'
data_test.loc[(data_test.FireplaceQu.isna()) & (data_test['1stFlrSF'] < 1060), 'FireplaceQu'] = 'Po'

In [274]:
#data_test.drop(data_test[data_test.GarageYrBlt == 2207].index, inplace=True)
data_test.loc[data_test.GarageYrBlt == 2207, 'GarageYrBlt'] = 2007

In [275]:
data_test.drop(['Id'], axis=1, inplace=True)
data_test = data_test.reset_index(drop=True)

In [276]:
data_test = data_test.astype({'BsmtFinSF1': np.int64})
data_test = data_test.astype({'BsmtUnfSF': np.int64})
data_test = data_test.astype({'TotalBsmtSF': np.int64})
data_test = data_test.astype({'BsmtFullBath': np.int64})
data_test = data_test.astype({'BsmtHalfBath': np.int64})
data_test = data_test.astype({'GarageYrBlt': np.int64})
data_test = data_test.astype({'GarageCars': np.int64})
data_test = data_test.astype({'GarageArea': np.int64})
data_test = data_test.astype({'LotFrontage': np.int64})
data_test = data_test.astype({'MasVnrArea': np.int64})

In [277]:
#data_test.info()

In [278]:
real_cols_test = ['LotFrontage', 'LotArea', 'YearBuilt', 'YearRemodAdd', 'MasVnrArea', 'BsmtFinSF1', 'BsmtUnfSF',
             'TotalBsmtSF', '1stFlrSF', '2ndFlrSF', 'GrLivArea', 'GarageYrBlt', 'GarageArea', 'WoodDeckSF', 
             'OpenPorchSF', 'EnclosedPorch']
cat_cols_test = ['MSSubClass', 'OverallQual', 'OverallCond', 'BsmtFullBath', 'BsmtHalfBath', 'FullBath', 'HalfBath',
            'BedroomAbvGr', 'KitchenAbvGr', 'TotRmsAbvGrd', 'Fireplaces', 'GarageCars', 'MoSold', 'YrSold', 
            'MSZoning', 'LotShape', 'LandContour', 'LotConfig', 'LandSlope', 'Neighborhood', 'Condition1', 'BldgType', 
            'HouseStyle', 'RoofStyle', 'Exterior1st', 'Exterior2nd', 'MasVnrType', 'ExterQual', 'ExterCond', 
            'Foundation', 'BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2', 'HeatingQC', 
            'CentralAir', 'Electrical', 'KitchenQual', 'Functional', 'FireplaceQu', 'GarageType', 'GarageFinish', 
            'GarageQual', 'PavedDrive', 'SaleType', 'SaleCondition']

In [279]:
scaler_real_cols_test = pd.DataFrame(scaler.fit_transform(data_test[real_cols]), columns=scaler.get_feature_names_out())
label_cat_cols_test = data_test[cat_cols].apply(LabelEncoder().fit_transform)
#one_hot_cat_cols_test = pd.DataFrame(ohe.fit_transform(cat_cols_test).toarray(), columns=ohe.get_feature_names_out())

In [280]:
X_2 = pd.concat([scaler_real_cols_test, label_cat_cols_test], axis='columns')
X_2

LotFrontage   LotArea  YearBuilt  YearRemodAdd  MasVnrArea  BsmtFinSF1  \
0        0.581531  0.363929  -0.340945     -1.072885   -0.570584    0.063936   
1        0.630086  0.897861  -0.439695     -1.214908    0.040790    1.063714   
2        0.290200  0.809646   0.844059      0.678742   -0.570584    0.773668   
3        0.484421  0.032064   0.876976      0.678742   -0.457367    0.358376   
4       -1.215012 -0.971808   0.679475      0.394694   -0.570584   -0.386513   
...           ...       ...        ...           ...         ...         ...   
1454    -2.283227 -1.591330  -0.044694     -0.646813   -0.570584   -0.964407   
1455    -2.283227 -1.599808  -0.044694     -0.646813   -0.570584   -0.410684   
1456     4.465949  2.055150  -0.373861      0.584059   -0.570584    1.725105   
1457    -0.292463  0.125527   0.679475      0.394694   -0.570584   -0.223912   
1458     0.290200 -0.038790   0.712392      0.489377   -0.038462    0.701157   

      BsmtUnfSF  TotalBsmtSF  1stFlrSF  2ndFlrSF  ...  Electrical  \
0     -0.650914    -0.370351 -0.654561 -0.775254  ...           3   
1     -0.339701     0.639477  0.433298 -0.775254  ...           3   
2     -0.955261    -0.266431 -0.574165  0.891944  ...           3   
3     -0.527344    -0.270949 -0.579190  0.837243  ...           3   
4      1.058466     0.528780  0.310192 -0.775254  ...           3   
...         ...          ...       ...       ...  ...         ...   
1454  -0.019335    -1.129416 -1.533893  0.523306  ...           3   
1455  -0.595994    -1.129416 -1.533893  0.523306  ...           3   
1456  -1.268762     0.402269  0.169499 -0.775254  ...           3   
1457   0.047026    -0.302577 -0.468645 -0.775254  ...           3   
1458  -0.724140    -0.112811 -0.403324  1.612573  ...           3   

      KitchenQual  Functional  FireplaceQu  GarageType  GarageFinish  \
0               3           6            3           1             3   
1               2           6            4           1             3   
2               3           6            4           1             0   
3               2           6            2           1             0   
4               2           6            4           1             2   
...           ...         ...          ...         ...           ...   
1454            3           6            3           6             1   
1455            3           6            3           4             3   
1456            3           6            4           5             3   
1457            3           6            3           6             1   
1458            3           6            4           1             0   

      GarageQual  PavedDrive  SaleType  SaleCondition  
0              4           2         8              4  
1              4           2         8              4  
2              4           2         8              4  
3              4           2         8              4  
4              4           2         8              4  
...          ...         ...       ...            ...  
1454           2           2         8              4  
1455           4           2         8              0  
1456           4           2         8              0  
1457           2           2         8              4  
1458           4           2         8              4  

[1459 rows x 63 columns]

In [376]:
y_pred_2 = xgb.predict(X_2)

In [377]:
y_pred_2[5:11]

array([181374.95, 184982.38, 181672.66, 223553.4 , 132819.  , 255076.23],
      dtype=float32)

In [373]:
submission = pd.read_csv('C:/Users/markc/Downloads/houses/sample_submission.csv')

In [374]:
submission['SalePrice'] = y_pred_2

In [375]:
submission[5:11]

Id      SalePrice
5   1466  173017.896891
6   1467  174987.229392
7   1468  166638.013689
8   1469  181117.125855
9   1470  120342.851810
10  1471  196327.435209

In [316]:
submission.to_csv('xgb_house_2.csv', index=None)